# Analyse Cryptomonnaie avec Binance Vision

Ce notebook utilise Binance Vision pour télécharger de gros datasets historiques de cryptomonnaies.

In [8]:
# ===========================================
# PARAMÈTRES DE CONFIGURATION
# ===========================================

# Durée d'analyse (en jours) - Binance Vision est optimisé pour de grandes périodes
DUREE_JOURS = 30

# Intervalle des données
# Options: 1s, 1m, 3m, 5m, 15m, 30m, 1h, 2h, 4h, 6h, 8h, 12h, 1d, 3d, 1w, 1M
INTERVAL = '1m'

# Symbole à analyser
SYMBOL = 'BTCUSDT'

print(f"Configuration:")
print(f"- Symbole: {SYMBOL}")
print(f"- Durée d'analyse: {DUREE_JOURS} jours")
print(f"- Intervalle: {INTERVAL}")
print(f"- Source: Binance Vision (données historiques)")
print()

Configuration:
- Symbole: BTCUSDT
- Durée d'analyse: 30 jours
- Intervalle: 1m
- Source: Binance Vision (données historiques)



In [9]:
# ===========================================
# IMPORTS ET FONCTIONS
# ===========================================

import pandas as pd
import requests
from datetime import datetime, timedelta
import time
import os
import zipfile
from io import BytesIO
import warnings
warnings.filterwarnings('ignore')

def download_binance_vision_data(symbol=SYMBOL, interval=INTERVAL, days_back=DUREE_JOURS):
    """
    Télécharge les données historiques depuis Binance Vision pour de gros datasets
    """
    print(f"Utilisation de Binance Vision pour télécharger {symbol} - {interval}")
    print(f"Période: {days_back} jours")
    print()
    
    # Calculer les dates nécessaires
    end_date = datetime.now()
    start_date = end_date - timedelta(days=days_back)
    
    all_data = []
    current_date = start_date
    success_count = 0
    total_periods = 0
    
    while current_date <= end_date:
        # Format de date pour l'URL Binance Vision
        date_str = current_date.strftime('%Y-%m-%d')
        
        # URL pour les données journalières
        url = f"https://data.binance.vision/data/spot/daily/klines/{symbol}/{interval}/{symbol}-{interval}-{date_str}.zip"
        
        print(f"Téléchargement: {date_str}", end=" ")
        
        try:
            response = requests.get(url, timeout=30)
            
            if response.status_code == 200:
                # Extraire le fichier CSV du ZIP
                with zipfile.ZipFile(BytesIO(response.content)) as zip_file:
                    csv_filename = f"{symbol}-{interval}-{date_str}.csv"
                    if csv_filename in zip_file.namelist():
                        csv_content = zip_file.read(csv_filename)
                        
                        # Lire le CSV
                        df_day = pd.read_csv(BytesIO(csv_content), header=None, names=[
                            'timestamp', 'open', 'high', 'low', 'close', 'volume',
                            'close_time', 'quote_asset_volume', 'number_of_trades',
                            'taker_buy_base_asset_volume', 'taker_buy_quote_asset_volume', 'ignore'
                        ])
                        
                        all_data.append(df_day)
                        success_count += 1
                        total_periods += len(df_day)
                        print(f"✓ ({len(df_day)} périodes)")
                    else:
                        print(f"⚠ Fichier CSV non trouvé")
            else:
                print(f"⚠ Non disponible (HTTP {response.status_code})")
                
        except requests.exceptions.RequestException as e:
            print(f"✗ Erreur réseau")
        except zipfile.BadZipFile:
            print(f"✗ ZIP corrompu")
        except Exception as e:
            print(f"✗ Erreur: {str(e)[:50]}")
        
        current_date += timedelta(days=1)
        time.sleep(0.1)  # Pause pour éviter la surcharge
    
    print(f"\nRésumé du téléchargement:")
    print(f"- Jours avec succès: {success_count}/{(end_date - start_date).days + 1}")
    print(f"- Total des périodes: {total_periods}")
    
    if all_data:
        # Combiner toutes les données
        combined_df = pd.concat(all_data, ignore_index=True)
        return combined_df.to_dict('records')
    else:
        print("Aucune donnée récupérée via Binance Vision")
        return []

def create_dataframe(data, symbol_name):
    if not data:
        print(f"Aucune donnée disponible pour {symbol_name}")
        return pd.DataFrame()
        
    df = pd.DataFrame(data, columns=[
        'timestamp', 'open', 'high', 'low', 'close', 'volume',
        'close_time', 'quote_asset_volume', 'number_of_trades',
        'taker_buy_base_asset_volume', 'taker_buy_quote_asset_volume', 'ignore'
    ])
    
    # Conversion des types
    for col in ['open', 'high', 'low', 'close', 'volume']:
        df[col] = df[col].astype(float)
    
    # Gestion des timestamps - Binance Vision utilise différents formats
    print("Conversion des timestamps...")
    timestamp_converted = False
    
    # Vérifier le format des timestamps en examinant quelques valeurs
    sample_timestamps = df['timestamp'].head(3).astype(str)
    print(f"Échantillon de timestamps: {list(sample_timestamps)}")
    
    try:
        # Essai avec millisecondes (format standard)
        df['timestamp'] = pd.to_datetime(df['timestamp'], unit='ms')
        timestamp_converted = True
        print("✓ Timestamps convertis depuis millisecondes")
    except (ValueError, pd.errors.OutOfBoundsDatetime, OverflowError):
        try:
            # Essai avec microsecondes (nouveau format depuis janvier 2025)
            print("⚠ Tentative conversion depuis microsecondes...")
            df['timestamp'] = pd.to_datetime(df['timestamp'], unit='us')
            timestamp_converted = True
            print("✓ Timestamps convertis depuis microsecondes")
        except (ValueError, pd.errors.OutOfBoundsDatetime, OverflowError):
            try:
                # Essai avec secondes
                print("⚠ Tentative conversion depuis secondes...")
                df['timestamp'] = pd.to_datetime(df['timestamp'], unit='s')
                timestamp_converted = True
                print("✓ Timestamps convertis depuis secondes")
            except (ValueError, pd.errors.OutOfBoundsDatetime, OverflowError):
                try:
                    # Si les valeurs sont trop grandes, diviser par 1000000 (microsecondes vers secondes)
                    print("⚠ Tentative correction des timestamps (division par 1M)...")
                    df['timestamp'] = pd.to_datetime(df['timestamp'] / 1000000, unit='s')
                    timestamp_converted = True
                    print("✓ Timestamps corrigés et convertis")
                except (ValueError, pd.errors.OutOfBoundsDatetime, OverflowError):
                    print("✗ Impossible de convertir les timestamps")
    
    if not timestamp_converted:
        print(f"✗ Erreur: Impossible de traiter les timestamps pour {symbol_name}")
        return pd.DataFrame()
    
    # Vérifier la plausibilité des dates
    min_date = df['timestamp'].min()
    max_date = df['timestamp'].max()
    
    if min_date.year < 2009 or max_date.year > 2030:
        print(f"⚠ Dates suspectes détectées: {min_date} à {max_date}")
    
    df.set_index('timestamp', inplace=True)
    
    # Supprimer les doublons et trier
    df = df[~df.index.duplicated(keep='first')].sort_index()
    
    # Affichage des informations adaptées à l'intervalle
    if len(df) > 0:
        print(f"\nDonnées {symbol_name} traitées:")
        print(f"Période: {df.index.min().strftime('%Y-%m-%d %H:%M')} à {df.index.max().strftime('%Y-%m-%d %H:%M')}")
        print(f"Nombre de périodes ({INTERVAL}): {len(df):,}")
        
        # Calculs selon l'intervalle
        if INTERVAL.endswith('s'):
            seconds_per_period = int(INTERVAL[:-1])
            minutes = len(df) * seconds_per_period / 60
            hours = minutes / 60
            days = hours / 24
            print(f"Équivalent: {minutes:,.0f} minutes, {hours:,.1f} heures, {days:.1f} jours")
        elif INTERVAL.endswith('m'):
            minutes_per_period = int(INTERVAL[:-1])
            hours = len(df) * minutes_per_period / 60
            days = hours / 24
            print(f"Équivalent: {hours:,.1f} heures, {days:.1f} jours")
        elif INTERVAL.endswith('h'):
            hours_per_period = int(INTERVAL[:-1])
            hours = len(df) * hours_per_period
            days = hours / 24
            print(f"Équivalent: {hours:,.1f} heures, {days:.1f} jours")
        elif INTERVAL == '1d':
            print(f"Équivalent: {len(df)} jours")
        
        print(f"Prix minimum: ${df['low'].min():.2f}")
        print(f"Prix maximum: ${df['high'].max():.2f}")
        print(f"Volume total: {df['volume'].sum():,.2f} {symbol_name.replace('USDT', '')}")
    
    return df

print("Fonctions chargées avec succès.")

Fonctions chargées avec succès.


In [10]:
# ===========================================
# TÉLÉCHARGEMENT DES DONNÉES
# ===========================================

print(f"=== Récupération {SYMBOL} via Binance Vision ===\n")

# Téléchargement des données
btc_data = download_binance_vision_data(SYMBOL, INTERVAL, DUREE_JOURS)

# Création du DataFrame
df_btc = create_dataframe(btc_data, SYMBOL)

if len(df_btc) > 0:
    print(f"\nPremières lignes {SYMBOL} (intervalle {INTERVAL}):")
    print(df_btc.head())
    
    print(f"\nDernières lignes:")
    print(df_btc.tail())
else:
    print(f"\n⚠ Aucune donnée disponible pour {SYMBOL}")
    print("Suggestions:")
    print("- Vérifiez que le symbole est correct (ex: BTCUSDT, ETHUSDT)")
    print("- Essayez avec une période plus récente")
    print("- Certains intervalles peuvent ne pas être disponibles pour toutes les dates")

=== Récupération BTCUSDT via Binance Vision ===

Utilisation de Binance Vision pour télécharger BTCUSDT - 1m
Période: 30 jours

Téléchargement: 2025-08-04 ✓ (1440 périodes)
Téléchargement: 2025-08-05 ✓ (1440 périodes)
Téléchargement: 2025-08-06 ✓ (1440 périodes)
Téléchargement: 2025-08-07 ✓ (1440 périodes)
Téléchargement: 2025-08-08 ✓ (1440 périodes)
Téléchargement: 2025-08-09 ✓ (1440 périodes)
Téléchargement: 2025-08-10 ✓ (1440 périodes)
Téléchargement: 2025-08-11 ✓ (1440 périodes)
Téléchargement: 2025-08-12 ✓ (1440 périodes)
Téléchargement: 2025-08-13 ✓ (1440 périodes)
Téléchargement: 2025-08-14 ✓ (1440 périodes)
Téléchargement: 2025-08-15 ✓ (1440 périodes)
Téléchargement: 2025-08-16 ✓ (1440 périodes)
Téléchargement: 2025-08-17 ✓ (1440 périodes)
Téléchargement: 2025-08-18 ✓ (1440 périodes)
Téléchargement: 2025-08-19 ✓ (1440 périodes)
Téléchargement: 2025-08-20 ✓ (1440 périodes)
Téléchargement: 2025-08-21 ✓ (1440 périodes)
Téléchargement: 2025-08-22 ✓ (1440 périodes)
Téléchargement: 2

In [11]:
# ===========================================
# VISUALISATION INTERACTIVE
# ===========================================

import plotly.graph_objects as go
from plotly.subplots import make_subplots

if len(df_btc) > 0:
    # Création de sous-graphiques
    fig = make_subplots(
        rows=2, cols=1,
        shared_xaxes=True,
        vertical_spacing=0.05,
        row_heights=[0.7, 0.3],
        specs=[[{"secondary_y": False}],
               [{"secondary_y": False}]]
    )

    # Graphique en chandeliers (prix)
    fig.add_trace(
        go.Candlestick(
            x=df_btc.index,
            open=df_btc['open'],
            high=df_btc['high'],
            low=df_btc['low'],
            close=df_btc['close'],
            name=f"{SYMBOL} Prix",
            increasing_line_color='#00c851',
            decreasing_line_color='#ff4444'
        ), 
        row=1, col=1
    )

    # Graphique des volumes
    fig.add_trace(
        go.Bar(
            x=df_btc.index,
            y=df_btc['volume'],
            name="Volume",
            marker_color='rgba(0, 150, 255, 0.6)',
            marker_line_color='rgba(0, 150, 255, 0.8)',
            marker_line_width=0.5
        ), 
        row=2, col=1
    )

    # Configuration du layout
    fig.update_layout(
        title={
            'text': f"{SYMBOL} - Données Binance Vision ({INTERVAL}, {DUREE_JOURS} jours)",
            'x': 0.5,
            'xanchor': 'center',
            'font': {'size': 16}
        },
        height=800,
        showlegend=False,
        xaxis_rangeslider_visible=False,
        template="plotly_white",
        margin=dict(l=50, r=50, t=80, b=50)
    )

    # Configuration des axes
    fig.update_yaxes(title_text="Prix (USD)", row=1, col=1)
    fig.update_yaxes(title_text="Volume", row=2, col=1)

    # Affichage
    config = {
        'displayModeBar': True,
        'displaylogo': False,
        'modeBarButtonsToRemove': ['pan2d', 'lasso2d']
    }

    print(f"Affichage du graphique {SYMBOL} avec {len(df_btc):,} périodes...")
    fig.show(config=config)
else:
    print("Impossible d'afficher le graphique: aucune donnée disponible.")

Affichage du graphique BTCUSDT avec 43,200 périodes...


In [12]:
# ===========================================
# ANALYSE STATISTIQUE DE BASE
# ===========================================

if len(df_btc) > 0:
    print(f"=== ANALYSE STATISTIQUE {SYMBOL} ===")
    print()
    
    # Statistiques de base
    print("Prix (USD):")
    print(f"- Prix moyen: ${df_btc['close'].mean():.2f}")
    print(f"- Prix médian: ${df_btc['close'].median():.2f}")
    print(f"- Écart-type: ${df_btc['close'].std():.2f}")
    print(f"- Min: ${df_btc['low'].min():.2f}")
    print(f"- Max: ${df_btc['high'].max():.2f}")
    print()
    
    # Calcul des rendements
    df_btc['returns'] = df_btc['close'].pct_change()
    
    print("Rendements:")
    print(f"- Rendement moyen: {df_btc['returns'].mean()*100:.4f}% par période")
    print(f"- Volatilité: {df_btc['returns'].std()*100:.4f}% par période")
    print(f"- Meilleur rendement: {df_btc['returns'].max()*100:.2f}%")
    print(f"- Pire rendement: {df_btc['returns'].min()*100:.2f}%")
    print()
    
    # Performance globale
    total_return = (df_btc['close'].iloc[-1] / df_btc['close'].iloc[0] - 1) * 100
    print("Performance globale:")
    print(f"- Prix initial: ${df_btc['close'].iloc[0]:.2f}")
    print(f"- Prix final: ${df_btc['close'].iloc[-1]:.2f}")
    print(f"- Rendement total: {total_return:.2f}%")
    print()
    
    # Volume
    print("Volume:")
    symbol_base = SYMBOL.replace('USDT', '').replace('BUSD', '')
    print(f"- Volume moyen: {df_btc['volume'].mean():,.2f} {symbol_base}")
    print(f"- Volume médian: {df_btc['volume'].median():,.2f} {symbol_base}")
    print(f"- Volume total: {df_btc['volume'].sum():,.2f} {symbol_base}")
    print(f"- Nombre de trades moyen: {df_btc['number_of_trades'].mean():,.0f}")
    
else:
    print("Impossible de générer les statistiques: aucune donnée disponible.")

=== ANALYSE STATISTIQUE BTCUSDT ===

Prix (USD):
- Prix moyen: $114645.56
- Prix médian: $114807.91
- Écart-type: $3651.30
- Min: $107255.00
- Max: $124474.00

Rendements:
- Rendement moyen: -0.0001% par période
- Volatilité: 0.0465% par période
- Meilleur rendement: 1.01%
- Pire rendement: -1.24%

Performance globale:
- Prix initial: $114291.93
- Prix final: $111240.01
- Rendement total: -2.67%

Volume:
- Volume moyen: 10.71 BTC
- Volume médian: 6.06 BTC
- Volume total: 462,538.64 BTC
- Nombre de trades moyen: 1,851


In [13]:
# ===========================================
# SAUVEGARDE DES DONNÉES (OPTIONNEL)
# ===========================================

if len(df_btc) > 0:
    # Nom du fichier avec timestamp
    timestamp = datetime.now().strftime('%Y%m%d_%H%M%S')
    filename = f"{SYMBOL}_{INTERVAL}_{DUREE_JOURS}d_{timestamp}.csv"
    
    # Sauvegarder en CSV
    df_btc.to_csv(filename)
    print(f"Données sauvegardées dans: {filename}")
    print(f"Taille du fichier: {os.path.getsize(filename) / (1024*1024):.2f} MB")
    
    # Affichage des informations du fichier
    print(f"\nContenu du fichier:")
    print(f"- {len(df_btc):,} lignes de données")
    print(f"- {len(df_btc.columns)} colonnes")
    print(f"- Période couverte: {(df_btc.index.max() - df_btc.index.min()).days} jours")
else:
    print("Aucune donnée à sauvegarder.")

Données sauvegardées dans: BTCUSDT_1m_30d_20250903_215023.csv
Taille du fichier: 6.23 MB

Contenu du fichier:
- 43,200 lignes de données
- 12 colonnes
- Période couverte: 29 jours
